In [1]:
import pprint
import pymongo
import json
import connector
from dotenv import load_dotenv
load_dotenv()
import os
from pymongo import MongoClient
user = os.getenv("USER")
password = os.getenv("PASSWORD")
client = pymongo.MongoClient("mongodb+srv://"+ user +":"+ password +"@cluster0-doqes.mongodb.net/test?retryWrites=true&w=majority")
db = connector.connect()
collection_trafic = db.vehicules


In [2]:
print(collection_trafic.find().count())

600000


D:\ProgramData\Anaconda\lib\site-packages\ipykernel_launcher.py:1: DeprecationWarning: count is deprecated. Use Collection.count_documents instead.
  """Entry point for launching an IPython kernel.


In [3]:
pprint.pprint(list(collection_trafic.find()[0:5]))

[{'_id': ObjectId('5ed3ed8fd59082dd24ba102c'),
  'nb_vehicules': 58,
  'num_arete': 0,
  'num_jour': 0,
  'num_periode': 1,
  'plage_horaire': 'm'},
 {'_id': ObjectId('5ed3ed8fd59082dd24ba102d'),
  'nb_vehicules': 32,
  'num_arete': 0,
  'num_jour': 0,
  'num_periode': 0,
  'plage_horaire': 'm'},
 {'_id': ObjectId('5ed3ed8fd59082dd24ba102e'),
  'nb_vehicules': 27,
  'num_arete': 0,
  'num_jour': 0,
  'num_periode': 3,
  'plage_horaire': 'm'},
 {'_id': ObjectId('5ed3ed8fd59082dd24ba102f'),
  'nb_vehicules': 41,
  'num_arete': 0,
  'num_jour': 0,
  'num_periode': 2,
  'plage_horaire': 'm'},
 {'_id': ObjectId('5ed3ed8fd59082dd24ba1030'),
  'nb_vehicules': 15,
  'num_arete': 0,
  'num_jour': 0,
  'num_periode': 4,
  'plage_horaire': 'm'}]


In [4]:
collection_trafic.insert_one({"num_arete":501})
print(collection_trafic.find_one({"num_arete":501}))

{'_id': ObjectId('5ed74fce26d2af9ab0396be1'), 'num_arete': 501}


In [5]:
collection_trafic.delete_one({"num_arete": 501})
print(collection_trafic.find_one({"num_arete": 501}))

None


In [6]:
vehicules_par_plage = {"m":0, "s":0}
for trafic in collection_trafic.find({"$or":[{"plage_horaire":"m"}, {"plage_horaire":"s"}]}):
    plage = trafic["plage_horaire"]
    vehicules_par_plage[plage] += trafic["nb_vehicules"]
print(vehicules_par_plage)

{'m': 19720247, 's': 28191853}


In [7]:
pipeline = [
    {
        "$group": 
        { 
            "_id": { "plage": "$plage_horaire"}, 
            "total": { "$sum": "$nb_vehicules"} 
        } 
    }
]
vehicules_par_plage = collection_trafic.aggregate(pipeline)
pprint.pprint(list(vehicules_par_plage))

[{'_id': {'plage': 'm'}, 'total': 19720247},
 {'_id': {'plage': 's'}, 'total': 28191853}]


In [14]:
import datetime
from datetime import timedelta, date
print("Hello World")
data_stamped = []

for trafic in collection_trafic.find():
    try :
        jour = trafic['num_jour']
    except KeyError:
        print(trafic)
        continue
    minute = trafic['num_periode']
    plage = trafic['plage_horaire']

    custom_date = datetime.datetime(2020,1,1)

    if plage == 'm' :
        heure = 0
        if minute >= 60 :
            heure = 1
            minute = minute - 60
        custom_date = datetime.datetime(2020,1,1+jour, 7 + heure, minute)

    if plage == 's' :
        heure = 0
        if minute >= 60 :
            heure = 1
            minute = minute - 60
        custom_date = datetime.datetime(2020,1,1+jour, 17 + heure, minute)
    #date_str = str(custom_date)

    row = { "num_arete":trafic['num_arete'],"date":custom_date, "nb_vehicules":trafic['nb_vehicules']}


    data_stamped.append(row)

print(len(data_stamped))

vehicules_stamped = db.vehicules_stamped
vehicules_stamped.delete_many({})

print(db.vehicules_stamped.find().count())

vehicules_stamped.insert_many(data_stamped)

print(db.vehicules_stamped.find().count())

Hello World
600000


D:\ProgramData\Anaconda\lib\site-packages\ipykernel_launcher.py:42: DeprecationWarning: count is deprecated. Use Collection.count_documents instead.


0
600000


D:\ProgramData\Anaconda\lib\site-packages\ipykernel_launcher.py:46: DeprecationWarning: count is deprecated. Use Collection.count_documents instead.


In [9]:
print(db.vehicules_stamped.find().count())

600000


D:\ProgramData\Anaconda\lib\site-packages\ipykernel_launcher.py:1: DeprecationWarning: count is deprecated. Use Collection.count_documents instead.
  """Entry point for launching an IPython kernel.


In [15]:
for row in vehicules_stamped.find() :
    print(row["date"])

2020-01-01 07:01:00
2020-01-01 07:00:00
2020-01-01 07:03:00
2020-01-01 07:02:00
2020-01-01 07:04:00
2020-01-01 07:05:00
2020-01-01 07:07:00
2020-01-01 07:08:00
2020-01-01 07:09:00
2020-01-01 07:11:00
2020-01-01 07:06:00
2020-01-01 07:10:00
2020-01-01 07:12:00
2020-01-01 07:13:00
2020-01-01 07:14:00
2020-01-01 07:15:00
2020-01-01 07:17:00
2020-01-01 07:16:00
2020-01-01 07:25:00
2020-01-01 07:26:00
2020-01-01 07:27:00
2020-01-01 07:28:00
2020-01-01 07:29:00
2020-01-01 07:30:00
2020-01-01 07:31:00
2020-01-01 07:32:00
2020-01-01 07:33:00
2020-01-01 07:34:00
2020-01-01 07:35:00
2020-01-01 07:36:00
2020-01-01 07:37:00
2020-01-01 07:38:00
2020-01-01 07:39:00
2020-01-01 07:40:00
2020-01-01 07:41:00
2020-01-01 07:42:00
2020-01-01 07:18:00
2020-01-01 07:19:00
2020-01-01 07:20:00
2020-01-01 07:21:00
2020-01-01 07:22:00
2020-01-01 07:23:00
2020-01-01 07:24:00
2020-01-01 07:43:00
2020-01-01 07:44:00
2020-01-01 07:45:00
2020-01-01 07:46:00
2020-01-01 07:48:00
2020-01-01 07:49:00
2020-01-01 07:50:00


2020-01-05 07:22:00
2020-01-05 07:23:00
2020-01-05 07:24:00
2020-01-05 07:26:00
2020-01-05 07:25:00
2020-01-05 07:27:00
2020-01-05 07:28:00
2020-01-05 07:30:00
2020-01-05 07:31:00
2020-01-05 07:29:00
2020-01-05 07:33:00
2020-01-05 07:32:00
2020-01-05 07:34:00
2020-01-05 07:35:00
2020-01-05 07:36:00
2020-01-05 07:37:00
2020-01-05 07:38:00
2020-01-05 07:39:00
2020-01-05 07:40:00
2020-01-05 07:41:00
2020-01-05 07:42:00
2020-01-05 07:43:00
2020-01-05 07:45:00
2020-01-05 07:44:00
2020-01-05 07:46:00
2020-01-05 07:47:00
2020-01-05 07:48:00
2020-01-05 07:49:00
2020-01-05 07:51:00
2020-01-05 07:52:00
2020-01-05 07:50:00
2020-01-05 07:53:00
2020-01-05 07:55:00
2020-01-05 07:54:00
2020-01-05 07:56:00
2020-01-05 07:57:00
2020-01-05 07:58:00
2020-01-05 08:00:00
2020-01-05 07:59:00
2020-01-05 08:01:00
2020-01-05 08:02:00
2020-01-05 08:04:00
2020-01-05 08:05:00
2020-01-05 08:06:00
2020-01-05 08:03:00
2020-01-05 08:08:00
2020-01-05 08:07:00
2020-01-05 08:09:00
2020-01-05 08:10:00
2020-01-05 08:11:00


2020-01-03 08:42:00
2020-01-03 08:44:00
2020-01-03 08:43:00
2020-01-03 08:46:00
2020-01-03 08:47:00
2020-01-03 08:45:00
2020-01-03 08:48:00
2020-01-03 08:49:00
2020-01-03 08:50:00
2020-01-03 08:51:00
2020-01-03 08:53:00
2020-01-03 08:52:00
2020-01-03 08:55:00
2020-01-03 08:54:00
2020-01-03 08:56:00
2020-01-03 08:57:00
2020-01-03 08:58:00
2020-01-03 08:59:00
2020-01-03 17:00:00
2020-01-03 17:01:00
2020-01-03 17:02:00
2020-01-03 17:03:00
2020-01-03 17:05:00
2020-01-03 17:04:00
2020-01-03 17:07:00
2020-01-03 17:06:00
2020-01-03 17:08:00
2020-01-03 17:09:00
2020-01-03 17:10:00
2020-01-03 17:11:00
2020-01-03 17:12:00
2020-01-03 17:13:00
2020-01-03 17:14:00
2020-01-03 17:15:00
2020-01-03 17:16:00
2020-01-03 17:17:00
2020-01-03 17:19:00
2020-01-03 17:20:00
2020-01-03 17:21:00
2020-01-03 17:18:00
2020-01-03 17:23:00
2020-01-03 17:24:00
2020-01-03 17:22:00
2020-01-03 17:25:00
2020-01-03 17:26:00
2020-01-03 17:28:00
2020-01-03 17:27:00
2020-01-03 17:29:00
2020-01-03 17:30:00
2020-01-03 17:32:00


2020-01-03 18:21:00
2020-01-03 18:22:00
2020-01-03 18:23:00
2020-01-03 18:24:00
2020-01-03 18:25:00
2020-01-03 18:27:00
2020-01-03 18:28:00
2020-01-03 18:26:00
2020-01-03 18:29:00
2020-01-03 18:30:00
2020-01-03 18:31:00
2020-01-03 18:32:00
2020-01-03 18:33:00
2020-01-03 18:34:00
2020-01-03 18:35:00
2020-01-03 18:36:00
2020-01-03 18:37:00
2020-01-03 18:39:00
2020-01-03 18:38:00
2020-01-03 18:40:00
2020-01-03 18:41:00
2020-01-03 18:42:00
2020-01-03 18:43:00
2020-01-03 18:44:00
2020-01-03 18:45:00
2020-01-03 18:46:00
2020-01-03 18:47:00
2020-01-03 18:48:00
2020-01-03 18:49:00
2020-01-03 18:50:00
2020-01-03 18:51:00
2020-01-03 18:52:00
2020-01-03 18:53:00
2020-01-03 18:54:00
2020-01-03 18:55:00
2020-01-03 18:56:00
2020-01-03 18:57:00
2020-01-03 18:58:00
2020-01-03 18:59:00
2020-01-04 07:01:00
2020-01-04 07:00:00
2020-01-04 07:02:00
2020-01-04 07:03:00
2020-01-04 07:04:00
2020-01-04 07:05:00
2020-01-04 07:06:00
2020-01-04 07:08:00
2020-01-04 07:09:00
2020-01-04 07:10:00
2020-01-04 07:07:00


2020-01-04 07:32:00
2020-01-04 07:33:00
2020-01-04 07:34:00
2020-01-04 07:35:00
2020-01-04 07:36:00
2020-01-04 07:37:00
2020-01-04 07:39:00
2020-01-04 07:38:00
2020-01-04 07:40:00
2020-01-04 07:42:00
2020-01-04 07:41:00
2020-01-04 07:43:00
2020-01-04 07:44:00
2020-01-04 07:46:00
2020-01-04 07:45:00
2020-01-04 07:47:00
2020-01-04 07:48:00
2020-01-04 07:49:00
2020-01-04 07:50:00
2020-01-04 07:51:00
2020-01-04 07:52:00
2020-01-04 07:53:00
2020-01-04 07:54:00
2020-01-04 07:55:00
2020-01-04 07:56:00
2020-01-04 07:57:00
2020-01-04 07:58:00
2020-01-04 08:00:00
2020-01-04 07:59:00
2020-01-04 08:02:00
2020-01-04 08:01:00
2020-01-04 08:03:00
2020-01-04 08:05:00
2020-01-04 08:04:00
2020-01-04 08:06:00
2020-01-04 08:08:00
2020-01-04 08:07:00
2020-01-04 08:10:00
2020-01-04 08:09:00
2020-01-04 08:11:00
2020-01-04 08:12:00
2020-01-04 08:13:00
2020-01-04 08:14:00
2020-01-04 08:15:00
2020-01-04 08:16:00
2020-01-04 08:17:00
2020-01-04 08:18:00
2020-01-04 08:19:00
2020-01-04 08:20:00
2020-01-04 08:21:00


...

2020-01-01 07:30:00
2020-01-01 07:31:00
2020-01-01 07:32:00
2020-01-01 07:34:00
2020-01-01 07:33:00
2020-01-01 07:35:00
2020-01-01 07:36:00
2020-01-01 07:37:00
2020-01-01 07:38:00
2020-01-01 07:39:00
2020-01-01 07:41:00
2020-01-01 07:40:00
2020-01-01 07:42:00
2020-01-01 07:43:00
2020-01-01 07:44:00
2020-01-01 07:45:00
2020-01-01 07:47:00
2020-01-01 07:46:00
2020-01-01 07:48:00
2020-01-01 07:49:00
2020-01-01 07:50:00
2020-01-01 07:51:00
2020-01-01 07:53:00
2020-01-01 07:52:00
2020-01-01 07:54:00
2020-01-01 07:55:00
2020-01-01 07:56:00
2020-01-01 07:57:00
2020-01-01 07:58:00
2020-01-01 07:59:00
2020-01-01 08:00:00
2020-01-01 08:01:00
2020-01-01 08:02:00
2020-01-01 08:03:00
2020-01-01 08:04:00
2020-01-01 08:05:00
2020-01-01 08:06:00
2020-01-01 08:07:00
2020-01-01 08:08:00
2020-01-01 08:09:00
2020-01-01 08:10:00
2020-01-01 08:11:00
2020-01-01 08:12:00
2020-01-01 08:13:00
2020-01-01 08:14:00
2020-01-01 08:15:00
2020-01-01 08:16:00
2020-01-01 08:17:00
2020-01-01 08:18:00
2020-01-01 08:19:00


2020-01-01 17:10:00
2020-01-01 17:11:00
2020-01-01 17:12:00
2020-01-01 17:13:00
2020-01-01 17:14:00
2020-01-01 17:15:00
2020-01-01 17:17:00
2020-01-01 17:16:00
2020-01-01 17:18:00
2020-01-01 17:19:00
2020-01-01 17:20:00
2020-01-01 17:21:00
2020-01-01 17:22:00
2020-01-01 17:23:00
2020-01-01 17:24:00
2020-01-01 17:25:00
2020-01-01 17:26:00
2020-01-01 17:27:00
2020-01-01 17:28:00
2020-01-01 17:29:00
2020-01-01 17:30:00
2020-01-01 17:31:00
2020-01-01 17:33:00
2020-01-01 17:32:00
2020-01-01 17:34:00
2020-01-01 17:35:00
2020-01-01 17:36:00
2020-01-01 17:37:00
2020-01-01 17:38:00
2020-01-01 17:39:00
2020-01-01 17:41:00
2020-01-01 17:40:00
2020-01-01 17:42:00
2020-01-01 17:43:00
2020-01-01 17:44:00
2020-01-01 17:45:00
2020-01-01 17:46:00
2020-01-01 17:47:00
2020-01-01 17:48:00
2020-01-01 17:49:00
2020-01-01 17:50:00
2020-01-01 17:52:00
2020-01-01 17:53:00
2020-01-01 17:54:00
2020-01-01 17:55:00
2020-01-01 17:56:00
2020-01-01 17:57:00
2020-01-01 17:58:00
2020-01-01 18:00:00
2020-01-01 18:01:00


2020-01-01 18:49:00
2020-01-01 18:50:00
2020-01-01 18:51:00
2020-01-01 18:52:00
2020-01-01 18:53:00
2020-01-01 18:55:00
2020-01-01 18:54:00
2020-01-01 18:56:00
2020-01-01 18:58:00
2020-01-01 18:57:00
2020-01-01 18:59:00
2020-01-02 07:00:00
2020-01-02 07:01:00
2020-01-02 07:02:00
2020-01-02 07:03:00
2020-01-02 07:04:00
2020-01-02 07:05:00
2020-01-02 07:07:00
2020-01-02 07:06:00
2020-01-02 07:08:00
2020-01-02 07:09:00
2020-01-02 07:10:00
2020-01-02 07:11:00
2020-01-02 07:13:00
2020-01-02 07:12:00
2020-01-02 07:15:00
2020-01-02 07:14:00
2020-01-02 07:16:00
2020-01-02 07:17:00
2020-01-02 07:18:00
2020-01-02 07:19:00
2020-01-02 07:20:00
2020-01-02 07:21:00
2020-01-02 07:22:00
2020-01-02 07:23:00
2020-01-02 07:24:00
2020-01-02 07:25:00
2020-01-02 07:26:00
2020-01-02 07:28:00
2020-01-02 07:27:00
2020-01-02 07:29:00
2020-01-02 07:30:00
2020-01-02 07:31:00
2020-01-02 07:32:00
2020-01-02 07:33:00
2020-01-02 07:34:00
2020-01-02 07:35:00
2020-01-02 07:36:00
2020-01-02 07:37:00
2020-01-02 07:38:00


2020-01-02 08:29:00
2020-01-02 08:30:00
2020-01-02 08:31:00
2020-01-02 08:32:00
2020-01-02 08:33:00
2020-01-02 08:34:00
2020-01-02 08:35:00
2020-01-02 08:37:00
2020-01-02 08:36:00
2020-01-02 08:38:00
2020-01-02 08:39:00
2020-01-02 08:40:00
2020-01-02 08:42:00
2020-01-02 08:43:00
2020-01-02 08:44:00
2020-01-02 08:46:00
2020-01-02 08:45:00
2020-01-02 08:47:00
2020-01-02 08:41:00
2020-01-02 08:48:00
2020-01-02 08:49:00
2020-01-02 08:51:00
2020-01-02 08:50:00
2020-01-02 08:52:00
2020-01-02 08:53:00
2020-01-02 08:54:00
2020-01-02 08:55:00
2020-01-02 08:56:00
2020-01-02 08:57:00
2020-01-02 08:58:00
2020-01-02 08:59:00
2020-01-02 17:00:00
2020-01-02 17:01:00
2020-01-02 17:02:00
2020-01-02 17:03:00
2020-01-02 17:04:00
2020-01-02 17:05:00
2020-01-02 17:06:00
2020-01-02 17:07:00
2020-01-02 17:08:00
2020-01-02 17:09:00
2020-01-02 17:10:00
2020-01-02 17:11:00
2020-01-02 17:12:00
2020-01-02 17:13:00
2020-01-02 17:14:00
2020-01-02 17:15:00
2020-01-02 17:17:00
2020-01-02 17:18:00
2020-01-02 17:19:00


KeyboardInterrupt: 

In [ ]:
matin = 0
soir = 0

for row in vehicules_stamped.find():
    if row["date"].hour >= 7 and row["date"].hour < 9:
        matin += int(row["nb_vehicules"])
    else:
        soir += int(row["nb_vehicules"])
        
print("Matin: "+ str(matin))
print("Soir: "+ str(soir))